In [1]:
!awk '/^[>;]/ { if (seq) { print seq }; seq=""; print } /^[^>;]/ { seq = seq $0 } END { print seq }' ../../A.fasta > ../../A.tmp 
#!sed 's/ /_/g;N;s/\n/,/g;s/|/,/g;s/>//g' > ../../B.csv
!sed -i 's/ /_/g;N;s/\n/,/g;s/|/,/g' ../../A.tmp
!awk -F , 'NF == 10' <../../A.tmp > ../../A.csv

In [2]:
import numpy as np
import pandas as pd
import sys
import re
import csv
import collections as co
import itertools as it
import umap
import hdbscan
import time 
import scipy.spatial.distance as ssd
#from memory_profiler import memory_usage

In [3]:
class vectorizer(object):
    
    def __init__(self, k = 7, convert = 0):
    
        self.k = k
        self.convert = convert
        self.exist = co.defaultdict(int) 
        self.keys = list(self.exist.keys())
        self.col = len(self.keys)
        self.row = 0
        self.matrix = np.empty((self.row, self.col, ),dtype = "float32")
        self.amino = co.defaultdict(str, {
            'AAA':'K', 'AAC':'N', 'AAG':'K', 'AAT':'N',
            'ACA':'T', 'ACC':'T', 'ACG':'T', 'ACT':'T',
            'AGA':'R', 'AGC':'S', 'AGG':'R', 'AGT':'S',
            'ATA':'I', 'ATC':'I', 'ATG':'M', 'ATT':'I',
            'CAA':'Q', 'CAC':'H', 'CAG':'Q', 'CAT':'H',
            'CCA':'P', 'CCC':'P', 'CCG':'P', 'CCT':'P',
            'CGA':'R', 'CGC':'R', 'CGG':'R', 'CGT':'R',
            'CTA':'L', 'CTC':'L', 'CTG':'L', 'CTT':'L',
            'GAA':'E', 'GAC':'D', 'GAG':'E', 'GAT':'D',
            'GCA':'A', 'GCC':'A', 'GCG':'A', 'GCT':'A',
            'GGA':'G', 'GGC':'G', 'GGG':'G', 'GGT':'G',
            'GTA':'V', 'GTC':'V', 'GTG':'V', 'GTT':'V',    
            'TAA':'Y', 'TAC':'*', 'TAG':'*', 'TAT':'Y',
            'TCA':'S', 'TCC':'S', 'TCG':'S', 'TCT':'S',
            'TGA':'*', 'TGC':'C', 'TGG':'W', 'TGT':'C',
            'TTA':'L', 'TTC':'F', 'TTG':'L', 'TTT':'F'
        })
                
    def translate(self, read):
    
        chain = ''

        for i in range(len(read) - 2):
            trip = read[i:i+3]
            chain += self.amino[trip]

        return(chain)
    
    
    def adjust_to_data(self, infile):
    
        self.row = infile.shape[0]
            
        for line, read in infile.itertuples(index=True, name=None):

            if self.convert == 1:
                seq = self.translate(read)
                del read

                num = len(seq) - self.k + 1

                for i in range(num):
                    kmer = seq[i:i+self.k]
                    self.exist[kmer] = 0

            else:
                seq = read
                del read

                num = len(seq) - self.k + 1

                if re.match('^[ACGT]*$', seq): 
                    for i in range(num):
                        kmer = seq[i:i+self.k]
                        self.exist[kmer] = 0
                else:
                    for i in range(num):
                        kmer = seq[i:i+self.k]
                        if re.match('^[ACGT]*$', kmer): 
                            self.exist[kmer] = 0
            
        self.keys = list(self.exist.keys())
        self.col = len(self.keys)
        self.matrix = np.empty((self.row, self.col, ), dtype="float32")
        
        del seq
    
    def calculate_frequence(self, infile):
        
        for line, read in infile.itertuples(index=True, name=None): 
                 
            if self.convert == 1:
                seq = self.translate(read)
                del read

                counts = self.exist.copy()
                num = len(seq) - self.k + 1

                for i in range(num):
                    kmer = seq[i:i+self.k]
                    counts[kmer] += 1

            else:
                seq = read
                del read

                counts = self.exist.copy()
                num = len(seq) - self.k + 1

                if re.match('^[ACGT]*$', seq): 
                    for i in range(num):
                        kmer = seq[i:i+self.k]
                        counts[kmer] += 1
                else:
                    for i in range(num):
                        kmer = seq[i:i+self.k]
                        if re.match('^[ACGT]*$', kmer): 
                            counts[kmer] += 1

            vector = np.array(list(counts.values()), dtype = "float32")/num

            self.matrix[line] = vector
            
            counts.clear()
            del vector
            del seq
            del counts
    
    
    def get_keys(self):
        
        return(self.keys)
    
    
    def get_matrix(self):
        
        return(self.matrix)

In [4]:
#def main():

print("Read input and settings file.", end = ' ')

infile = '../../A.csv'   
setfile = 'Input/settings.csv'
outpath = 'Output/'

settings = pd.read_csv(setfile, sep = ',', na_filter = False, index_col = 0)
upload = pd.read_csv(infile, sep = ',', na_filter = False, header = None)
upload.columns = ['accession', 'strain', 'segment', 'protein', 'genus', 'subtype', 'date', 'host', 'curation', 'genome']
upload.query('curation == "Pass"', inplace = True)
segments = settings.index.values.tolist()
clusters = co.defaultdict(list)
exec_time = 0
increment = 0

print("Finished.")

segments = [4]
for segment in segments:

    print(f"Starting calculations for segment {segment}:")

    start_clust = time.perf_counter()
    parameter = settings.loc[segment].to_list()
    setting = [para if type(para) == str else para.item() for para in parameter]

    subset = upload.query('segment == @segment').reset_index()

    sequence = subset[['genome']].copy()
    accession = subset[['accession']].copy()
    subtype = subset[['subtype']].copy()

    print("- Nucleotide k-mer frequency calculation.", end = ' ')

    freq_nt = vectorizer(k = setting[0], convert = 0)
    freq_nt.adjust_to_data(sequence)
    freq_nt.calculate_frequence(sequence)

    matrix_nt = freq_nt.get_matrix()
    keys_nt = freq_nt.get_keys()

    del freq_nt

    print("Finished.")

    print("- Running UMAP for dimension reduction.", end = ' ')

    matrix_nt_red = umap.UMAP(
        n_neighbors = setting[1],
        min_dist = setting[2],
        n_components = setting[3],
        random_state = setting[4],
        metric = setting[5],
    ).fit_transform(matrix_nt)

    del matrix_nt

    print("Finished.")

    print("- Aminoacid k-mer frequency calculation.", end = ' ')

    freq_aa = vectorizer(k = setting[6], convert = 1)
    freq_aa.adjust_to_data(sequence)
    freq_aa.calculate_frequence(sequence)

    matrix_aa = freq_aa.get_matrix()
    keys_aa = freq_aa.get_keys()

    del freq_aa

    print("Finished.")

    print("- Running UMAP for dimension reduction.", end = ' ')

    matrix_aa_red = umap.UMAP(
        n_neighbors = setting[7],
        min_dist = setting[8],
        n_components = setting[9],
        random_state = setting[10],
        metric = setting[11],
    ).fit_transform(matrix_aa)

    del matrix_aa

    print("Finished.")

    matrix = pd.concat([accession, pd.DataFrame(matrix_aa_red), pd.DataFrame(matrix_nt_red)], axis=1, copy = False, ignore_index = False).set_index('accession')

    print("- Running HDBscan for clustering.", end = ' ')

    matrix_clust = hdbscan.HDBSCAN(
        min_samples = setting[12], #larger the value the more conservative the clustering (more points will be declared as noise)
        min_cluster_size = setting[13], #minimum size that can become a cluster
        cluster_selection_epsilon = setting[14], #don't seperate clusters with a distance less than value
        alpha = setting[15], #don't mess with this
        gen_min_span_tree=True,
    ).fit(matrix)

    print("Finished.")

    print("- Centroid extraction.", end = ' ')

    clusterlabel = matrix_clust.labels_

    blank = pd.DataFrame(zip(clusterlabel, ['False'] * len(clusterlabel)), columns = ['cluster', 'centroid'])
    clusters[segment] = pd.concat([blank, subtype, accession], axis=1, copy = False).set_index('accession')

    num = clusters[segment]['cluster'].max()+1
    values = ['True']*num
    accessions = []
    exclude = []
    include = []
    overall_mean=0
    subs = co.defaultdict(list)

    for i in range(num):

        query = clusters[segment].query('cluster == @i')
        match = query.index.values.tolist()
        sub = matrix.filter(items = match, axis=0)
        dist = ssd.cdist(sub, sub, metric = setting[16])
        inner_mean = pd.DataFrame(dist, columns = match, index = match, dtype = 'float32').mean()
        accessions.append(inner_mean.idxmin())
        overall_mean = overall_mean + inner_mean.mean()

        for sub in query['subtype'].tolist():
            if re.match('^[H][0-9]+N[0-9]+$', sub): 
                subs['H'].append(re.search('[H][0-9]+', sub).group(0))
                subs['N'].append(re.search('[N][0-9]+', sub).group(0))
            else:
                subs['X'].append('X0')
                subs['X'].append('X0')

        if len(set(subs['H'])) == 1 and len(set(subs['N'])) == 1:
            exclude.append(2)
            if 'X' not in subs.keys():
                include.append(2)
        elif len(set(subs['H'])) == 1:
            exclude.append(1)
            if 'X' not in subs.keys():
                include.append(1)
        elif len(set(subs['N'])) == 1:
            exclude.append(0)
            if 'X' not in subs.keys():
                include.append(0)

        subs.clear()

    centroids = pd.DataFrame(values, columns=['centroid'], index = accessions)

    clusters[segment].loc[clusters[segment]['cluster'] != -1, ['cluster']] = clusters[segment].loc[clusters[segment]['cluster'] != -1, ['cluster']] + increment
    clusters[segment].update(centroids)

    increment += num - 1

    print("Finished.")

    stop_clust = time.perf_counter()
    exec_clust = stop_clust - start_clust
    exec_time = exec_time + exec_clust

    print(f"- Clustering done in {exec_clust:0.2f} seconds.")
    diagnostic = co.Counter(clusterlabel)
    print(f"- {str(len(clusterlabel))} sequences, {str(diagnostic[-1])} unclustered, {str(len(set(diagnostic))-1)} cluster.")
    print(f"- Mean of inner cluster distance mean {overall_mean/num:0.10f}")
    print(f"- {exclude.count(0) + exclude.count(2)}({include.count(0) + include.count(2)}) clusters containing matching NA types.")
    print(f"- {exclude.count(1) + exclude.count(2)}({include.count(1) + include.count(2)}) clusters containing matching HA types.")
    print("Finished.")

result = pd.concat(clusters)
result.index.set_names(["segment", "accession"], inplace=True)
result.reset_index(level = "segment", inplace=True)  
result.sort_values(by=['segment', 'cluster', 'subtype'], inplace = True)
result.to_csv(outpath + 'cluster_wo_align.csv', index=True, header=True, sep=',', mode='w')
print(f"Overall execution time {exec_time:0.2f} seconds.")

Read input and settings file. Finished.
Starting calculations for segment 4:
- Nucleotide k-mer frequency calculation. Finished.
- Running UMAP for dimension reduction. Finished.
- Aminoacid k-mer frequency calculation. Finished.
- Running UMAP for dimension reduction. Finished.
- Running HDBscan for clustering. Finished.
- Centroid extraction. Finished.
- Clustering done in 1062.76 seconds.
- 55281 sequences, 46 unclustered, 816 cluster.
- Mean of inner cluster distance mean 0.0000594674
- 619(549) clusters containing matching NA types.
- 814(608) clusters containing matching HA types.
Finished.
Overall execution time 1062.76 seconds.


In [14]:
if __name__ == "__main__":

    main()
    #memory = memory_usage(main)
    #print(f"Maximum memory used: {max(memory)/1000:0.2f} Gb.")

Read input and settings file. Finished.
Starting calculations for segment 6:
- Nucleotide k-mer frequency calculation. Finished.
- Running UMAP for dimension reduction. Finished.
- Aminoacid k-mer frequency calculation. Finished.
- Running UMAP for dimension reduction. Finished.
- Running HDBscan for clustering. Finished.
- Centroid extraction. Finished.
- Clustering done in 977.08 seconds.
- 55075 sequences, 25 unclustered, 940 cluster.
- Mean of inner cluster distance mean 0.0000845859
- 936(709) clusters containing matching NA types.
- 729(652) clusters containing matching HA types.
Finished.
Overall execution time 977.08 seconds.


In [16]:
x = matrix_clust.single_linkage_tree_.to_pandas()

In [194]:
set(diagnostic)

{-1,
 0,
 1,
 2,
 3,
 4,
 5,
 6,
 7,
 8,
 9,
 10,
 11,
 12,
 13,
 14,
 15,
 16,
 17,
 18,
 19,
 20,
 21,
 22,
 23,
 24,
 25,
 26,
 27,
 28,
 29,
 30,
 31,
 32,
 33,
 34,
 35,
 36,
 37,
 38,
 39,
 40,
 41,
 42,
 43,
 44,
 45,
 46,
 47,
 48,
 49,
 50,
 51,
 52,
 53,
 54,
 55,
 56,
 57,
 58,
 59,
 60,
 61,
 62,
 63,
 64,
 65,
 66,
 67,
 68,
 69,
 70,
 71,
 72,
 73,
 74,
 75,
 76,
 77,
 78,
 79,
 80,
 81,
 82,
 83,
 84,
 85,
 86,
 87,
 88,
 89,
 90,
 91,
 92,
 93,
 94,
 95,
 96,
 97,
 98,
 99,
 100,
 101,
 102,
 103,
 104,
 105,
 106,
 107,
 108,
 109,
 110,
 111,
 112,
 113,
 114,
 115,
 116,
 117,
 118,
 119,
 120,
 121,
 122,
 123,
 124,
 125,
 126,
 127,
 128,
 129,
 130,
 131,
 132,
 133,
 134,
 135,
 136,
 137,
 138,
 139,
 140,
 141,
 142,
 143,
 144,
 145,
 146,
 147,
 148,
 149,
 150,
 151,
 152,
 153,
 154,
 155,
 156,
 157,
 158,
 159,
 160,
 161,
 162,
 163,
 164,
 165,
 166,
 167,
 168,
 169,
 170,
 171,
 172,
 173,
 174,
 175,
 176,
 177,
 178,
 179,
 180,
 181,
 182,
 183,
 

In [67]:
matrix_clust.single_linkage_tree_.to_pandas()

parent  left_child  right_child   distance     size
0       55281     31231.0      31232.0   0.000025      2.0
1       55282       108.0      28946.0   0.000042      2.0
2       55283      5466.0      11694.0   0.000045      2.0
3       55284     30723.0      36888.0   0.000049      2.0
4       55285      8914.0       8918.0   0.000049      2.0
...       ...         ...          ...        ...      ...
55275  110556    110520.0     110555.0  23.685131  55004.0
55276  110557    109852.0     110556.0  23.771735  55043.0
55277  110558    109847.0     110557.0  24.683127  55198.0
55278  110559    109712.0     110558.0  25.966437  55270.0
55279  110560     81247.0     110559.0  26.198130  55281.0

[55280 rows x 5 columns]

In [172]:
result

segment  cluster centroid subtype
accession                                   
>KC780781        4       -1    False    H1N1
>CY062210        4       -1    False    H1N1
>KX006018        4       -1    False    H1N1
>KY487123        4       -1    False    H1N1
>KF559390        4       -1    False    H1N1
...            ...      ...      ...     ...
>KT840328        4      814    False    H3N2
>KT841779        4      814    False    H3N2
>KT843119        4      814    False    H3N2
>KX412411        4      814    False    H3N2
>KT843938        4      814    False    H3N2

[55281 rows x 4 columns]

In [96]:
matrix_clust.single_linkage_tree_.get_clusters(20, min_cluster_size=2).max()

37

In [100]:
test = pd.concat([pd.DataFrame(clusterlabel2, columns = ['cluster']), subtype, accession], axis=1, copy = False).set_index('accession')

In [101]:
test

cluster subtype
accession                 
>J02176         28    H1N1
>CY021709       28    H1N1
>CY020285       28    H1N1
>CY083910       28    H1N1
>CY063606       28    H1N1
...            ...     ...
>KM374042       28    H7N9
>CY095721       28    H1N1
>CY095748       28    H1N1
>KF007060       28    H7N9
>KU217316       28    H9N2

[55281 rows x 2 columns]

In [75]:
test.query('cluster == 14')['subtype'].to_list()

['H10N3',
 'H10N3',
 'H10N3',
 'H10N3',
 'H10N3',
 'H10N3',
 'H10N3',
 'H10N3',
 'H10N3',
 'H10N3',
 'H10N3']

In [66]:
test[test['subtype'].str.contains('H2N')]

cluster subtype
accession                 
>CY191027       28    H2N1
>CY191035       28    H2N1
>MN552480       28    H2N1
>MN795016       28    H2N1
>LC041995       28    H2N1
...            ...     ...
>CY003855       28    H2N9
>MH501497       28    H2N9
>MN511811       28    H2N9
>KF258946       28    H2N9
>KF258944       28    H2N9

[514 rows x 2 columns]

In [198]:
test = pd.read_csv('Output/cluster_wo_align.csv', header=0, index_col=0)
test

segment  cluster  centroid subtype
accession                                    
>GU571155        6       -1     False    H1N1
>GU234175        6       -1     False    H1N1
>CY097854        6       -1     False    H1N1
>CY097862        6       -1     False    H1N1
>CY097870        6       -1     False    H1N1
...            ...      ...       ...     ...
>KX414587        6      926     False    H3N2
>KX414579        6      926     False    H3N2
>KX415050        6      926     False    H3N2
>KU591261        6      926     False    H3N2
>KX412992        6      926     False    H3N2

[55075 rows x 4 columns]

In [214]:
print(result.groupby('cluster')['subtype'].count())

cluster
-1       46
 0       11
 1       33
 2       39
 3       61
       ... 
 810     63
 811    297
 812      8
 813     15
 814    110
Name: subtype, Length: 816, dtype: int64


In [217]:
list(result.value_counts(subset=['cluster']) )

[1445,
 765,
 740,
 496,
 477,
 467,
 439,
 438,
 370,
 362,
 360,
 356,
 348,
 340,
 329,
 323,
 312,
 301,
 299,
 299,
 297,
 297,
 295,
 292,
 287,
 279,
 277,
 276,
 272,
 270,
 270,
 267,
 263,
 260,
 255,
 250,
 250,
 250,
 249,
 247,
 247,
 246,
 244,
 244,
 239,
 235,
 234,
 233,
 229,
 224,
 222,
 222,
 220,
 219,
 218,
 218,
 217,
 217,
 216,
 215,
 212,
 209,
 201,
 201,
 198,
 198,
 198,
 196,
 196,
 193,
 190,
 189,
 187,
 186,
 186,
 184,
 183,
 182,
 180,
 180,
 180,
 176,
 175,
 174,
 173,
 172,
 171,
 169,
 169,
 169,
 164,
 163,
 163,
 161,
 160,
 160,
 159,
 158,
 158,
 157,
 157,
 155,
 153,
 152,
 152,
 151,
 151,
 149,
 148,
 148,
 147,
 147,
 146,
 146,
 145,
 145,
 144,
 143,
 140,
 139,
 138,
 138,
 137,
 135,
 134,
 132,
 131,
 130,
 128,
 127,
 125,
 125,
 125,
 123,
 123,
 122,
 119,
 119,
 119,
 117,
 117,
 116,
 113,
 113,
 112,
 112,
 112,
 111,
 110,
 110,
 109,
 109,
 109,
 108,
 106,
 105,
 104,
 104,
 104,
 103,
 102,
 102,
 102,
 101,
 101,
 100,
 99

In [218]:
list(test.value_counts(subset=['cluster']))

[1205,
 749,
 717,
 668,
 586,
 516,
 504,
 471,
 414,
 404,
 388,
 387,
 381,
 349,
 341,
 341,
 339,
 331,
 330,
 324,
 321,
 317,
 299,
 298,
 297,
 290,
 268,
 264,
 257,
 248,
 246,
 235,
 231,
 227,
 227,
 219,
 215,
 212,
 208,
 207,
 207,
 206,
 206,
 205,
 205,
 202,
 199,
 198,
 198,
 198,
 196,
 196,
 194,
 193,
 187,
 179,
 178,
 178,
 178,
 175,
 175,
 174,
 173,
 170,
 169,
 169,
 169,
 168,
 165,
 165,
 165,
 164,
 163,
 163,
 163,
 161,
 161,
 159,
 159,
 157,
 156,
 155,
 154,
 152,
 152,
 151,
 148,
 144,
 144,
 143,
 142,
 142,
 142,
 141,
 141,
 141,
 140,
 139,
 139,
 139,
 138,
 138,
 136,
 134,
 132,
 132,
 132,
 132,
 132,
 129,
 129,
 126,
 126,
 126,
 125,
 125,
 122,
 122,
 121,
 121,
 120,
 117,
 117,
 117,
 115,
 115,
 114,
 112,
 112,
 111,
 110,
 109,
 108,
 108,
 108,
 106,
 106,
 106,
 106,
 105,
 105,
 104,
 104,
 104,
 103,
 103,
 103,
 102,
 102,
 102,
 102,
 102,
 101,
 101,
 101,
 100,
 100,
 99,
 98,
 97,
 97,
 96,
 96,
 96,
 96,
 95,
 95,
 95,
 9

In [201]:
test = pd.read_csv('Output/cluster_wo_align.csv', header=0, index_col=0)

exclude = []
subs = co.defaultdict(list)

for k in range(test['cluster'].max()+1):

    query = test.query('cluster == @k')

    for sub in query['subtype'].tolist():
        if re.match('^[H][0-9]+N[0-9]+$', sub): 
            subs['H'].append(re.search('[H][0-9]+', sub).group(0))
            subs['N'].append(re.search('[N][0-9]+', sub).group(0))
        
    if len(set(subs['H'])) == 1 and len(set(subs['N'])) == 1:
        #exclude.append(2)
        #print(f'{k}: {subs["H"][0]} {query.shape[0]}')
        pass
    elif len(set(subs['N'])) == 1:
        #exclude.append(1)
        #print(f'{k}: {subs["H"][0]} {query.shape[0]}')
        pass
    else:
        print(f'{k}: {", ".join(set(subs["N"]))} {query.shape[0]}')
    
    subs.clear()
#if exclude.count(0) + exclude.count(2) != cluster.max() and exclude.count(1) + exclude.count(2) != cluster.max():
#    print(exclude.count(0) + exclude.count(2), exclude.count(1) + exclude.count(2), cluster.max())
#    print(i)

526: N2, N1 32
666: N3, N1 104
877: N8, N2 187


In [207]:
test.query('cluster == 877')

segment  cluster  centroid subtype
accession                                    
>KT843599        6      877     False    H3N2
>KT844201        6      877     False    H3N2
>KT844209        6      877     False    H3N2
>KU590292        6      877     False    H3N2
>KU589717        6      877     False    H3N2
...            ...      ...       ...     ...
>KT843975        6      877     False    H3N2
>KU589523        6      877     False    H3N2
>KU589922        6      877     False    H3N2
>KU591624        6      877     False    H3N2
>MG925516        6      877     False    H3N8

[187 rows x 4 columns]

In [205]:
test.query('subtype == "H1N2"')

segment  cluster  centroid subtype
accession                                    
>KJ764773        6       97     False    H1N2
>KX960229        6      160     False    H1N2
>MF613961        6      160     False    H1N2
>MF092736        6      160     False    H1N2
>KY454591        6      160     False    H1N2
...            ...      ...       ...     ...
>KT828317        6      784     False    H1N2
>KJ640782        6      784     False    H1N2
>KJ640253        6      784     False    H1N2
>KJ605109        6      784     False    H1N2
>KU229965        6      784     False    H1N2

[1678 rows x 4 columns]

In [155]:
subs['H'].append('H1')

In [157]:
", ".join(subs['H'])

'H1, H1, H1, H1'

In [83]:
for i,j in enumerate(tree.to_pandas()['distance'].to_list()):
    print(i,j)

0 2.4634823448252536e-05
1 4.23930474016513e-05
2 4.513045702211532e-05
3 4.85154537344605e-05
4 4.872543911981022e-05
5 5.677549074262846e-05
6 5.825972148205054e-05
7 6.00775070504058e-05
8 6.0333322212233416e-05
9 6.040518323871408e-05
10 6.0682329351406525e-05
11 6.075385111863582e-05
12 6.145998340587608e-05
13 6.261081385176187e-05
14 6.314301956384126e-05
15 6.426697209768583e-05
16 6.510971328888978e-05
17 6.565578784568295e-05
18 6.602378816788498e-05
19 6.680247568293159e-05
20 6.875963506957762e-05
21 6.87718858936096e-05
22 7.002010812930961e-05
23 7.01472982249387e-05
24 7.041105037916116e-05
25 7.052472600323465e-05
26 7.130284350448587e-05
27 7.24986561715046e-05
28 7.612904670552662e-05
29 7.61701766564565e-05
30 7.714430020367265e-05
31 7.772014858659741e-05
32 7.774477181979305e-05
33 7.793403961888752e-05
34 7.960385944480957e-05
35 7.992058294417441e-05
36 7.999520700256831e-05
37 8.138771332703005e-05
38 8.303060739147622e-05
39 8.352576051077005e-05
40 8.411379615

1585 0.00023845958182515726
1586 0.00023846996021941778
1587 0.00023847982245875945
1588 0.000238495472642566
1589 0.00023856420837723317
1590 0.0002385732682815402
1591 0.00023862617365788812
1592 0.00023887542080097817
1593 0.00023888308939484532
1594 0.00023894966289389412
1595 0.00023898887971262716
1596 0.00023899162425872265
1597 0.00023912934810616746
1598 0.00023913179204882178
1599 0.0002392136181392245
1600 0.0002392186880628746
1601 0.00023926626616108685
1602 0.00023927908818845817
1603 0.00023935077684238755
1604 0.0002393588731667021
1605 0.00023945994007634573
1606 0.0002394683441395542
1607 0.00023954175533593634
1608 0.00023955632339282593
1609 0.00023956528124429214
1610 0.00023959881981332513
1611 0.0002396064203096253
1612 0.00023963645029111824
1613 0.00023972334969603955
1614 0.0002397701470705423
1615 0.00023979181145579643
1616 0.0002398654724066684
1617 0.0002398912204277918
1618 0.00023992706459516916
1619 0.0002400122946942893
1620 0.00024017938372744682
1621

3319 0.0004186668307909648
3320 0.0004189531279008064
3321 0.0004191151192997903
3322 0.0004192408395926933
3323 0.000419365008156379
3324 0.00041946989816045915
3325 0.00041956979815609743
3326 0.00041963593298687007
3327 0.0004201892244235602
3328 0.0004203533505968003
3329 0.0004203743488615885
3330 0.00042078816215396594
3331 0.0004208101595179967
3332 0.00042114537942263404
3333 0.00042124741645004245
3334 0.0004213111763574202
3335 0.0004216758702765309
3336 0.0004218120778934777
3337 0.0004220332274984458
3338 0.0004220437605020789
3339 0.000422242369557813
3340 0.0004224294966678502
3341 0.0004224716632720167
3342 0.0004227161449493154
3343 0.00042276643442699957
3344 0.00042278434582888245
3345 0.00042308455492035023
3346 0.00042317023964402294
3347 0.0004231772600364568
3348 0.0004232359246504185
3349 0.00042362126460298704
3350 0.000423682577711615
3351 0.00042435203503235047
3352 0.00042447093424174704
3353 0.00042472750971074417
3354 0.0004250675404208628
3355 0.0004253063

4881 0.0006793386032822074
4882 0.0006795709121494602
4883 0.0006795722729253755
4884 0.0006797397995425649
4885 0.0006800243820693307
4886 0.0006806569269249529
4887 0.0006806760194464724
4888 0.0006815564728995706
4889 0.0006816988970335703
4890 0.0006818228809500082
4891 0.0006818774390730569
4892 0.0006820601360981753
4893 0.0006821122556621727
4894 0.0006824863056801782
4895 0.000682566932523373
4896 0.0006832231436411031
4897 0.0006833501258726127
4898 0.0006834097235635185
4899 0.0006835574103292002
4900 0.0006838194975391574
4901 0.0006839713784906207
4902 0.0006841971609475822
4903 0.0006842879138470577
4904 0.0006843546166602558
4905 0.0006848171328552057
4906 0.0006852794742684683
4907 0.0006853844261955585
4908 0.0006855346985461295
4909 0.000685604016718381
4910 0.0006858193908041095
4911 0.0006863355688942527
4912 0.0006865734921049041
4913 0.0006865974039632839
4914 0.000686667652236638
4915 0.0006870307842384369
4916 0.0006872336041281392
4917 0.0006872506761529676
4918

6861 0.0011027488561665434
6862 0.0011028508231391986
6863 0.001102886709846361
6864 0.0011030021452491925
6865 0.0011031009466562626
6866 0.0011032169433148472
6867 0.001103267634243585
6868 0.0011033185581064997
6869 0.0011036442389437708
6870 0.0011036796821015328
6871 0.0011038638233072556
6872 0.0011039599263123214
6873 0.0011042319974094545
6874 0.0011042570442858187
6875 0.0011046675576570162
6876 0.0011047045380128625
6877 0.0011051219583513236
6878 0.0011053023535450538
6879 0.0011053839474928445
6880 0.0011056582316110463
6881 0.0011059830480106222
6882 0.001106022216103886
6883 0.0011063389270859411
6884 0.0011063891679159112
6885 0.0011065423004080579
6886 0.001106701287087213
6887 0.0011070904850183597
6888 0.0011087350079283906
6889 0.00111008593994932
6890 0.0011103662870693327
6891 0.0011103750480042605
6892 0.0011107103029790212
6893 0.0011107348987114765
6894 0.0011108537015803621
6895 0.001111075708469478
6896 0.0011113486047627397
6897 0.0011114108736612765
6898 0.0

...

48436 0.0769527388621915
48437 0.07696246104149485
48438 0.07696250661680548
48439 0.07697132621762942
48440 0.07697407821477423
48441 0.07698273364858668
48442 0.0769848798506427
48443 0.07700193103227913
48444 0.0770090166329052
48445 0.07701520613577978
48446 0.07704795549726791
48447 0.07710465714053885
48448 0.07711149656820661
48449 0.07711162157238599
48450 0.07711449410010535
48451 0.07712219560891682
48452 0.07712562412662607
48453 0.07713302579627836
48454 0.07713373563277946
48455 0.0771359270967653
48456 0.07713975056155918
48457 0.0771690437834083
48458 0.07716935971099781
48459 0.07717090284260458
48460 0.07717746755993367
48461 0.07718306069581325
48462 0.07718967572012646
48463 0.0771910584952198
48464 0.0772053776987206
48465 0.07720929180994329
48466 0.07722323994865235
48467 0.07722335914727646
48468 0.07722871103441849
48469 0.07723411222502226
48470 0.07725040179714684
48471 0.0772914491255551
48472 0.07729172255788534
48473 0.07730458405360924
48474 0.077312763839

50288 0.09554155122321233
50289 0.09555998677851378
50290 0.09556516439200094
50291 0.09556872283699801
50292 0.095571110740028
50293 0.09558716862383451
50294 0.09561421534195566
50295 0.0956199955802676
50296 0.09563607166618113
50297 0.09563797163754123
50298 0.09564342311114844
50299 0.09565006264566699
50300 0.09566767599710076
50301 0.09568068357317543
50302 0.09569391355960481
50303 0.09569679102289137
50304 0.09569792876580353
50305 0.09571373345258714
50306 0.09571660506823387
50307 0.09573528491540087
50308 0.09573838878038628
50309 0.0957468085806759
50310 0.09575028719425807
50311 0.09575088206364246
50312 0.09575241506924707
50313 0.09575645793434433
50314 0.0957592855268605
50315 0.09576359743535977
50316 0.0958192895125577
50317 0.09584277562525424
50318 0.09586204128336595
50319 0.09587096066130925
50320 0.09587714791661862
50321 0.0958927515477611
50322 0.09589351762631944
50323 0.09592183714639296
50324 0.09593084159662961
50325 0.0959464349208439
50326 0.095953056718

51680 0.11847358688964552
51681 0.11848106036258514
51682 0.11849258548125594
51683 0.11853683041801705
51684 0.11853839624177218
51685 0.11854754028625666
51686 0.11855474360893602
51687 0.11855806773151484
51688 0.11857786094722414
51689 0.11859857336818487
51690 0.1186083303129622
51691 0.11863035629281046
51692 0.118674681479962
51693 0.1186931527387369
51694 0.11875123582184961
51695 0.11876630000904827
51696 0.11880559125348443
51697 0.11883375773368982
51698 0.11886356635803565
51699 0.11886568274666744
51700 0.1189381794603092
51701 0.11894043942577351
51702 0.1189725509821287
51703 0.1190192272484953
51704 0.11902708717490419
51705 0.11903905990256596
51706 0.11904604296747301
51707 0.11908555067423446
51708 0.11908673381700782
51709 0.11911466823804018
51710 0.11912086867332565
51711 0.11915174263708532
51712 0.11916602792332434
51713 0.11921145907380276
51714 0.11928787128952005
51715 0.11929633296862693
51716 0.11932316702737492
51717 0.11932600386577132
51718 0.11939888803

53351 0.19253652112342348
53352 0.1928114941069672
53353 0.19284673069495753
53354 0.19290260880997734
53355 0.19298818227539047
53356 0.19312696109855268
53357 0.19314383777855784
53358 0.19324547667781927
53359 0.1934711286124821
53360 0.19347797161957872
53361 0.19357583072361725
53362 0.19364783949717926
53363 0.19371919181028663
53364 0.1939465124935278
53365 0.19395846759306723
53366 0.19399861211800173
53367 0.19405107468571792
53368 0.1942263721298386
53369 0.19439272298665736
53370 0.19454563482839024
53371 0.1945680012935874
53372 0.19478822181529248
53373 0.1950682922324516
53374 0.19539890814052882
53375 0.19548024983480425
53376 0.19551080256904843
53377 0.19561378862734163
53378 0.19567854443567922
53379 0.1959434755031492
53380 0.1959871449139412
53381 0.1959965441655772
53382 0.19625118036077804
53383 0.19664935142979267
53384 0.1967830651021863
53385 0.19695750504265463
53386 0.19720475829502734
53387 0.19720599058328492
53388 0.19721633158416174
53389 0.19737809251358

55020 10.256565059213807
55021 10.289325337267124
55022 10.306371087108275
55023 10.30641902933899
55024 10.320315649218118
55025 10.393423266987353
55026 10.411496736676279
55027 10.422545260587386
55028 10.451099830200109
55029 10.457425255957018
55030 10.553482064332696
55031 10.571326774306062
55032 10.598704702485357
55033 10.67952266480758
55034 10.756798771572381
55035 10.808389864918617
55036 10.85346238158517
55037 10.857421880367829
55038 10.92478216628942
55039 10.9414290595799
55040 10.952202456511468
55041 10.955931792430869
55042 10.956251933577965
55043 11.002896482046431
55044 11.040387205302768
55045 11.058186761464079
55046 11.063093246249172
55047 11.073636158436223
55048 11.076410604346862
55049 11.142286982528873
55050 11.17617218350243
55051 11.229390346468158
55052 11.331995172478436
55053 11.335298812912644
55054 11.35302986726331
55055 11.396958636808723
55056 11.402209380281489
55057 11.453595615583543
55058 11.460996034701102
55059 11.465292479813568
55060 11

In [80]:
9 % 10 == 0

False

In [166]:
matrix_clust.cluster_persistence_

array([8.45002497e-02, 1.03159146e-01, 5.68143970e-02, 6.54766879e-02,
       1.85530641e-02, 3.35243783e-02, 1.37058181e-02, 2.71087047e-02,
       2.79679313e-02, 2.91564591e-02, 7.69675088e-03, 3.32738028e-01,
       3.12570116e-02, 9.90944114e-03, 5.84428528e-03, 3.50888979e-02,
       2.53828771e-02, 3.27873095e-02, 3.05310331e-02, 5.64482158e-01,
       3.43338196e-02, 6.74534615e-03, 1.48159982e-01, 1.75373754e-01,
       1.85897132e-03, 1.91250513e-02, 2.00464323e-02, 5.16179409e-02,
       1.85371292e-02, 2.91956448e-01, 6.21349579e-02, 3.34757896e-03,
       2.70024990e-02, 4.23875614e-02, 2.42999789e-02, 5.01404241e-01,
       6.44468974e-03, 2.18262285e-02, 2.73101191e-03, 1.43301597e-02,
       5.62048867e-02, 5.92175874e-03, 3.70062850e-02, 9.75273931e-03,
       2.59865594e-03, 5.48043297e-05, 8.70523333e-03, 1.41150128e-02,
       4.89981202e-01, 1.02480026e-01, 6.39600263e-03, 1.88608753e-01,
       4.53721950e-03, 2.43776434e-03, 9.67732175e-02, 4.62061431e-01,
      

In [ ]:
clust